# Dates in timeseries models

In [1]:
import statsmodels.api as sm
import numpy as np
import pandas as pd

## Getting started

In [2]:
data = sm.datasets.sunspots.load()

Right now an annual date series must be datetimes at the end of the year.

In [3]:
from datetime import datetime
dates = sm.tsa.datetools.dates_from_range('1700', length=len(data.endog))

## Using Pandas

Make a pandas TimeSeries or DataFrame

In [4]:
endog = pd.Series(data.endog, index=dates)

Instantiate the model

In [5]:
ar_model = sm.tsa.AR(endog, freq='A')
pandas_ar_res = ar_model.fit(maxlag=9, method='mle', disp=-1)

/home/travis/build/statsmodels/statsmodels/statsmodels/tsa/ar_model.py:691: FutureWarning: 
statsmodels.tsa.AR has been deprecated in favor of statsmodels.tsa.AutoReg and
statsmodels.tsa.SARIMAX.

AutoReg adds the ability to specify exogenous variables, include time trends,
and add seasonal dummies. The AutoReg API differs from AR since the model is
treated as immutable, and so the entire specification including the lag
length must be specified when creating the model. This change is too
substantial to incorporate into the existing AR api. The function
ar_select_order performs lag length selection for AutoReg models.

AutoReg only estimates parameters using conditional MLE (OLS). Use SARIMAX to
estimate ARX and related models using full MLE via the Kalman Filter.

To silence this warning and continue using AR until it is removed, use:

import warnings
warnings.filterwarnings('ignore', 'statsmodels.tsa.ar_model.AR', FutureWarning)

  warnings.warn(AR_DEPRECATION_WARN, FutureWarning)


Out-of-sample prediction

In [6]:
pred = pandas_ar_res.predict(start='2005', end='2015')
print(pred)

2005-12-31    20.003283
2006-12-31    24.703988
2007-12-31    20.026129
2008-12-31    23.473646
2009-12-31    30.858563
2010-12-31    61.335427
2011-12-31    87.024648
2012-12-31    91.321189
2013-12-31    79.921544
2014-12-31    60.799430
2015-12-31    40.374784
Freq: A-DEC, dtype: float64


## Using explicit dates

In [7]:
ar_model = sm.tsa.AR(data.endog, dates=dates, freq='A')
ar_res = ar_model.fit(maxlag=9, method='mle', disp=-1)
pred = ar_res.predict(start='2005', end='2015')
print(pred)

[20.00328342 24.70398784 20.02612925 23.47364606 30.85856303 61.33542735
 87.02464842 91.32118867 79.9215437  60.79942985 40.37478415]


This just returns a regular array, but since the model has date information attached, you can get the prediction dates in a roundabout way.

In [8]:
print(ar_res.data.predict_dates)

DatetimeIndex(['2005-12-31', '2006-12-31', '2007-12-31', '2008-12-31',
               '2009-12-31', '2010-12-31', '2011-12-31', '2012-12-31',
               '2013-12-31', '2014-12-31', '2015-12-31'],
              dtype='datetime64[ns]', freq='A-DEC')


Note: This attribute only exists if predict has been called. It holds the dates associated with the last call to predict.